# <center> Analyse de la concentration de CO2, <center>

In [56]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime
from scipy import interpolate
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

Nous récupérons les données les plus récentes sur le site en pointant sur un fichier au format .csv, si cette récupération est possible nous enregistrons une copie de ce fichier. Si pour une raison quelconque nous n'arrivons pas a faire ce téléchargement, nous travaillons sur le dernières données téléchargé.

In [57]:
try:
    raw_data = pd.read_csv("https://scrippsco.ucsd.edu/assets/data/atmospheric/stations/"
                           "in_situ_co2/monthly/monthly_in_situ_co2_mlo.csv",skiprows=56)
except OSError as err:
    print("Erreur lors du téléchargement : {0}".format(err))
    print("Nous téléchargeons les dernières données enregistrer sur notre PC")
    raw_data = pd.read_csv("monthly_in_situ_co2_mlo")
except:
    print("Unexpected error:", sys.exc_info()[0])
    raise
else:
    raw_data.to_csv('monthly_in_situ_co2_mlo',index=True)

raw_data.head(5)
raw_data.tail(5)

Erreur lors du téléchargement : <urlopen error [Errno -2] Name or service not known>
Nous téléchargeons les dernières données enregistrer sur notre PC


Unnamed: 0                Excel                 [ppm]      [ppm]   \
0           0  1958    1     21200   1958.0411    -99.99      -99.99   
1           1  1958    2     21231   1958.1260    -99.99      -99.99   
2           2  1958    3     21259   1958.2027    315.70      314.44   
3           3  1958    4     21290   1958.2877    317.45      315.16   
4           4  1958    5     21320   1958.3699    317.51      314.71   

         [ppm]      [ppm]         [ppm]      [ppm].1  
0       -99.99     -99.99        -99.99       -99.99  
1       -99.99     -99.99        -99.99       -99.99  
2       316.19     314.91        315.70       314.44  
3       317.30     314.99        317.45       315.16  
4       317.86     315.06        317.51       314.71

Unnamed: 0                Excel                 [ppm]      [ppm]   \
751         751  2020    8     44058   2020.6230    -99.99      -99.99   
752         752  2020    9     44089   2020.7077    -99.99      -99.99   
753         753  2020   10     44119   2020.7896    -99.99      -99.99   
754         754  2020   11     44150   2020.8743    -99.99      -99.99   
755         755  2020   12     44180   2020.9563    -99.99      -99.99   

           [ppm]      [ppm]         [ppm]      [ppm].1  
751       -99.99     -99.99        -99.99       -99.99  
752       -99.99     -99.99        -99.99       -99.99  
753       -99.99     -99.99        -99.99       -99.99  
754       -99.99     -99.99        -99.99       -99.99  
755       -99.99     -99.99        -99.99       -99.99

Nous voyons que les noms des colonnes ne sont pas très représentatives, nous modifions  les noms des colonnes

In [58]:
raw_data.columns 
raw_data.columns = ['Yr','Mn','Date 1','Date 2','s1','s2','s3','s4','s5','s6','s7']
data = raw_data
data.head(5)

Index(['Unnamed: 0', '    ', '   ', '   Excel', '          ', '   [ppm]',
       '    [ppm] ', '      [ppm]', '    [ppm]', '       [ppm]',
       '    [ppm].1'],
      dtype='object')

Yr    Mn  Date 1  Date 2         s1      s2      s3      s4      s5  \
0   0  1958       1   21200  1958.0411  -99.99  -99.99  -99.99  -99.99   
1   1  1958       2   21231  1958.1260  -99.99  -99.99  -99.99  -99.99   
2   2  1958       3   21259  1958.2027  315.70  314.44  316.19  314.91   
3   3  1958       4   21290  1958.2877  317.45  315.16  317.30  314.99   
4   4  1958       5   21320  1958.3699  317.51  314.71  317.86  315.06   

       s6      s7  
0  -99.99  -99.99  
1  -99.99  -99.99  
2  315.70  314.44  
3  317.45  315.16  
4  317.51  314.71

Les données vide sont représentés par la valeur -99.99, nous remplaçons cette valeur par une valeur plus adéquate NaN dans une autre DataFrame

In [59]:
data = data.replace(-99.99,np.NaN);

On visualise les lignes dont une donnée colonne est manquante.

In [63]:
data[data.isnull().any(axis=1)]

Yr    Mn  Date 1  Date 2         s1  s2  s3      s4      s5      s6  \
0      0  1958       1   21200  1958.0411 NaN NaN     NaN     NaN     NaN   
1      1  1958       2   21231  1958.1260 NaN NaN     NaN     NaN     NaN   
5      5  1958       6   21351  1958.4548 NaN NaN  317.24  315.14  317.24   
9      9  1958      10   21473  1958.7890 NaN NaN  312.44  315.40  312.44   
73    73  1964       2   23422  1964.1257 NaN NaN  320.01  319.36  320.01   
74    74  1964       3   23451  1964.2049 NaN NaN  320.74  319.41  320.74   
75    75  1964       4   23482  1964.2896 NaN NaN  321.83  319.45  321.83   
745  745  2020       2   43876  2020.1257 NaN NaN     NaN     NaN     NaN   
746  746  2020       3   43905  2020.2049 NaN NaN     NaN     NaN     NaN   
747  747  2020       4   43936  2020.2896 NaN NaN     NaN     NaN     NaN   
748  748  2020       5   43966  2020.3716 NaN NaN     NaN     NaN     NaN   
749  749  2020       6   43997  2020.4563 NaN NaN     NaN     NaN     NaN   
750  750  2020       7   44027  2020.5383 NaN NaN     NaN     NaN     NaN   
751  751  2020       8   44058  2020.6230 NaN NaN     NaN     NaN     NaN   
752  752  2020       9   44089  2020.7077 NaN NaN     NaN     NaN     NaN   
753  753  2020      10   44119  2020.7896 NaN NaN     NaN     NaN     NaN   
754  754  2020      11   44150  2020.8743 NaN NaN     NaN     NaN     NaN   
755  755  2020      12   44180  2020.9563 NaN NaN     NaN     NaN     NaN   

         s7  
0       NaN  
1       NaN  
5    315.14  
9    315.40  
73   319.36  
74   319.41  
75   319.45  
745     NaN  
746     NaN  
747     NaN  
748     NaN  
749     NaN  
750     NaN  
751     NaN  
752     NaN  
753     NaN  
754     NaN  
755     NaN

On ajoute un index ' période'  à la DataFrame, cet index représente la période de mesure. 
Cette date est mise dans au format compréhensible par pandas. On visualise toutes les lignes qui seront supprimées.

In [64]:
data['period'] = [datetime.date(y,m,1) for y,m in zip(data['Yr'],data['Mn'])]
data = data.set_index('period')   
data = data.dropna().copy()


ValueError: year 0 is out of range